### Get job_id of data analytics in San Francisco

In [1]:
import requests
from bs4 import BeautifulSoup
import yaml
import logging
from multiprocessing import Pool, Manager
import requests
import yaml
import logging
from multiprocessing import Pool, Manager
import json
import time
import re
import pandas as pd
import numpy as np
# sql database
import pymysql
import warnings
import codecs
import stat

In [20]:
logging.getLogger().setLevel(logging.INFO)


with open('config.yml') as config_file:
    config = yaml.safe_load(config_file)


def list_jobs(search_term,country_code,page):
    str_length = len(search_term) + 3
    url='https://www.glassdoor.com/Job/{search_term}-SRCH_IL.0,13_IC{country_code}_KO14,{str_length}_IP{page}.htm'.format(search_term=search_term,country_code=country_code,str_length=str_length, page=page)

    html_page = requests.get(url, headers=config['headers']).text

    return html_page


def get_total_pages(html_page):
    soup = BeautifulSoup(html_page, 'html.parser')
    try:
        pages_text = soup.find_all("div", class_="cell middle hideMob padVertSm")[0].text
        total_pages = pages_text.split(' ')[-1]
        return int(total_pages)
    except IndexError:
        return 1


def get_job_ids(html_page):
    soup = BeautifulSoup(html_page, 'html.parser')
    jobs_list = soup.find_all("li", class_="jl")
    jobs_ids = []
    for job in jobs_list:
        jobs_ids.append(job.get('data-id'))
    return jobs_ids


def write_jobs_ids_to_file(jobs_ids):
    with open(config['jobs-ids-filename'], 'a') as dest_file:
        for job_id in jobs_ids:
            dest_file.write(job_id)
            dest_file.write('\n')


def worker(row,country_code,search_term):
    for page_count in range(1, 31):
        html_page = list_jobs(search_term,country_code,page_count)
        total_pages = get_total_pages(html_page)
        if page_count > total_pages:
            break
        logging.info('{}: extracting ids {},{},{}'.format(len(row),search_term,country_code,  page_count))
        jobs_ids = get_job_ids(html_page)
        row += jobs_ids



def execute():
    for country_code in config['country-code']:
        with Manager() as mgr:
            row = mgr.list([])

            params = []
            for search_term in config['search-terms']:
                params.append([row,country_code, search_term])

            with Pool() as p:
                p.starmap(worker, params)

            write_jobs_ids_to_file(row)
            time.sleep(3)


if __name__ == '__main__':
    execute()



INFO:root:0: extracting ids data-analyst,1147436,1
INFO:root:32: extracting ids data-scientist,1147436,1
INFO:root:64: extracting ids business-analyst,1147436,1
INFO:root:96: extracting ids data-analyst,1147436,2
INFO:root:128: extracting ids data-scientist,1147436,2
INFO:root:128: extracting ids business-analyst,1147436,2
INFO:root:192: extracting ids data-analyst,1147436,3
INFO:root:224: extracting ids business-analyst,1147436,3
INFO:root:256: extracting ids data-scientist,1147436,3
INFO:root:288: extracting ids data-analyst,1147436,4
INFO:root:320: extracting ids business-analyst,1147436,4
INFO:root:352: extracting ids data-scientist,1147436,4
INFO:root:384: extracting ids data-analyst,1147436,5
INFO:root:416: extracting ids business-analyst,1147436,5
INFO:root:448: extracting ids data-scientist,1147436,5
INFO:root:480: extracting ids business-analyst,1147436,6
INFO:root:512: extracting ids data-scientist,1147436,6
INFO:root:512: extracting ids data-analyst,1147436,6
INFO:root:576: 

In [3]:
with open("jobs_ids_0225.txt","r") as file:
    id_num=file.readlines()
len(id_num)

5406

In [6]:
for i in range(len(id_num)):
    id_num[i]=re.sub("\n","",id_num[i])
id_number=pd.DataFrame(id_num)
id_number.columns=['id']
unique_id=id_number["id"].unique()
len(unique_id)

1730

In [57]:
for i in range(1068,len(unique_id)):
    id_number=unique_id[i]
    url='https://www.glassdoor.com/Job/json/details.htm?jobListingId={number}'.format(number=id_number)
    filename=str("/Users/yiyingwang/Downloads/data_analyst/"+id_number+".htm")
    json_data = requests.get(url, headers=user_agent)
    json_file=json_data.text
    with open(filename,"w") as file:
        file.write(json_file)
    time.sleep(5)
    print(id_number+"success")

3416296417success
3166478924success
3476273662success
3478522339success
3423881371success
3480745525success
3407275250success
3324404005success
3482715857success
3484939370success
3456846631success
3493974323success
3449948666success
3484624859success
3493973829success
3307511180success
3365067721success
3466346545success
3476377240success
3494451342success
3470654491success
3360755446success
3486432089success
3503034907success
3483415990success
3462001471success
3233313749success
3466169497success
3406671109success
3423881244success
3437863140success
3430223566success
3492699164success
3444984756success
3400534529success
3502966340success
3476377259success
3496345521success
3481077421success
3187807955success
3498995258success
3492940772success
3400647854success
3503594916success
3480094773success
3484952083success
3499625100success
3459615865success
3439178975success
3425886080success
3436680907success
3449154604success
3473234779success
3480237813success
3454327476success
3205895502

In [62]:
filename=str("/Users/yiyingwang/Downloads/finalproject/data_analyst/"+str(unique_id[0])+".htm")
with open(filename,"r") as file:
    website=json.load(file)
website

{'benefits': {'benefitRatingDecimal': 0.0,
  'comments': [],
  'employerSummary': '<p>Competitive health packages to keep you healthy &amp; happy. We provide healthcare, dental &amp; optical both to you &amp; your dependents. Offering a weekly yoga class, daily group meditations, and healthy snacks - your well-being is a top priority for us.</p>',
  'highlights': [],
  'numRatings': 0},
 'breadCrumbs': [{'name': 'JOBS', 'url': '/Job/index.htm'}],
 'gaTrackerData': {'category': 10007,
  'empId': 2464640,
  'empName': 'Woebot Labs',
  'empSize': '1-50',
  'expired': False,
  'industry': 'Computer Hardware & Software',
  'industryId': 200060,
  'jobId': 3501649697,
  'jobTitle': 'Data Analyst',
  'location': 'San Francisco',
  'locationId': 1147401,
  'locationType': 'CITY',
  'pageRequestGuid': {'guid': '00000170808c471fada338937e7c8953',
   'guidValid': True,
   'part1': 1582704641823,
   'part2': -5934837677810742957},
  'sector': 'Information Technology',
  'sectorId': 10013},
 'heade

# BEFORE RUNNING THE FOLLOWING CODE
1. Please change the  "psw" to your local SQL password

In [2]:
psw = 'SQLpassword'

In [3]:
def create_sql_table(SQL_DB, SQL_TABLE, SQL_TABLE_DEF):
    try:
        #connect to server
        conn = pymysql.connect(host='localhost', user = 'root', password = psw)
        cursor = conn.cursor()

        query = "CREATE DATABASE IF NOT EXISTS " + SQL_DB + ";"
        print(query)
        cursor.execute(query);     
        query = "CREATE TABLE IF NOT EXISTS " + SQL_DB + "." + SQL_TABLE + " " + SQL_TABLE_DEF + ";";
        print(query)
        cursor.execute(query);
        cursor.close()
        conn.close()
    except IOError as e:
        print(e)
        pass

In [4]:
SQL_DB = "glassdoor"
SQL_TABLE_job = "job"
SQL_TABLE_DEF_job = "(" + \
        " jobID BIGINT(20) NOT NULL PRIMARY KEY" + \
        ",job_description LONGTEXT CHARACTER SET utf8 COLLATE utf8_unicode_ci" + \
        ",job_title VARCHAR(255)" + \
        ",companyID BIGINT(20)" + \
        ",companyName VARCHAR(255)" + \
        ")"
SQL_TABLE_company = "company"
SQL_TABLE_DEF_company = "(" + \
        " companyID BIGINT(20) NOT NULL PRIMARY KEY" + \
        ",companyName VARCHAR(255)" + \
        ",companySize VARCHAR(255)" + \
        ",location VARCHAR(255)" + \
        ",locationID BIGINT(20)" + \
        ",company_description LONGTEXT CHARACTER SET utf8 COLLATE utf8_unicode_ci" + \
        ",foundedyear INT(20)" + \
        ",headcount VARCHAR(255)" + \
        ",industry VARCHAR(255)" + \
        ",industryID BIGINT(20)" + \
        ",company_revenue VARCHAR(255)" + \
        ",sector VARCHAR(255)" + \
        ",sectorID BIGINT(20)" + \
        ",website VARCHAR(255)" + \
        ",type VARCHAR(255)" + \
        ",ceo_name VARCHAR(255)" + \
        ")"
SQL_TABLE_rating = "rating"
SQL_TABLE_DEF_rating = "(" + \
        " ratingID INT NOT NULL AUTO_INCREMENT PRIMARY KEY" + \
        ",companyID BIGINT(20)" + \
        ",ceo_name VARCHAR(255)" + \
        ",ceo_ratingsCount INT(20)" + \
        ",ceo_approval DECIMAL(10,3)" + \
        ",recommend_to_friend DECIMAL(10,3)" + \
        ",overall_starRating DECIMAL(10,3)" + \
        ")"
SQL_TABLE_salary = "salary"
SQL_TABLE_DEF_salary = "(" + \
        " salaryID INT NOT NULL AUTO_INCREMENT PRIMARY KEY" + \
        ",jobID BIGINT(20)" + \
        ",companyID BIGINT(20)" + \
        ",base_pay_count INT(20)" + \
        ",job_title VARCHAR(255)" + \
        ",pay_period VARCHAR(255)" + \
        ",pay_q10 DECIMAL(10,3)" + \
        ",pay_q90 DECIMAL(10,3)" + \
        ",salary_type VARCHAR(255)" + \
        ")"

In [5]:
create_sql_table(SQL_DB, SQL_TABLE_job, SQL_TABLE_DEF_job)
create_sql_table(SQL_DB, SQL_TABLE_company, SQL_TABLE_DEF_company)
create_sql_table(SQL_DB, SQL_TABLE_rating, SQL_TABLE_DEF_rating)
create_sql_table(SQL_DB, SQL_TABLE_salary, SQL_TABLE_DEF_salary)

CREATE DATABASE IF NOT EXISTS glassdoor;
CREATE TABLE IF NOT EXISTS glassdoor.job ( jobID BIGINT(20) NOT NULL PRIMARY KEY,job_description LONGTEXT CHARACTER SET utf8 COLLATE utf8_unicode_ci,job_title VARCHAR(255),companyID BIGINT(20),companyName VARCHAR(255));
CREATE DATABASE IF NOT EXISTS glassdoor;
CREATE TABLE IF NOT EXISTS glassdoor.company ( companyID BIGINT(20) NOT NULL PRIMARY KEY,companyName VARCHAR(255),companySize VARCHAR(255),location VARCHAR(255),locationID BIGINT(20),company_description LONGTEXT CHARACTER SET utf8 COLLATE utf8_unicode_ci,foundedyear INT(20),headcount VARCHAR(255),industry VARCHAR(255),industryID BIGINT(20),company_revenue VARCHAR(255),sector VARCHAR(255),sectorID BIGINT(20),website VARCHAR(255),type VARCHAR(255),ceo_name VARCHAR(255));


E:\Anaconda3\lib\site-packages\pymysql\cursors.py:170: Warning: (1007, "Can't create database 'glassdoor'; database exists")
  result = self._query(query)
E:\Anaconda3\lib\site-packages\pymysql\cursors.py:170: Warning: (3719, "'utf8' is currently an alias for the character set UTF8MB3, but will be an alias for UTF8MB4 in a future release. Please consider using UTF8MB4 in order to be unambiguous.")
  result = self._query(query)
E:\Anaconda3\lib\site-packages\pymysql\cursors.py:170: Warning: (3778, "'utf8_unicode_ci' is a collation of the deprecated character set UTF8MB3. Please consider using UTF8MB4 with an appropriate collation instead.")
  result = self._query(query)


CREATE DATABASE IF NOT EXISTS glassdoor;
CREATE TABLE IF NOT EXISTS glassdoor.rating ( ratingID INT NOT NULL AUTO_INCREMENT PRIMARY KEY,companyID BIGINT(20),ceo_name VARCHAR(255),ceo_ratingsCount INT(20),ceo_approval DECIMAL(10,3),recommend_to_friend DECIMAL(10,3),overall_starRating DECIMAL(10,3));
CREATE DATABASE IF NOT EXISTS glassdoor;
CREATE TABLE IF NOT EXISTS glassdoor.salary ( salaryID INT NOT NULL AUTO_INCREMENT PRIMARY KEY,jobID BIGINT(20),companyID BIGINT(20),base_pay_count INT(20),job_title VARCHAR(255),pay_period VARCHAR(255),pay_q10 DECIMAL(10,3),pay_q90 DECIMAL(10,3),salary_type VARCHAR(255));


# Extract interested values from .htm files and insert values into 4 sql tables

In [5]:
#job
def job(website):
    jobid=website['gaTrackerData']['jobId']
    jobtitle=re.sub("'","''",website['gaTrackerData']['jobTitle'])
    description_o=website['job']['description']
    description=re.sub("'","''",description_o)
    if("empName" in website["gaTrackerData"].keys()):
        empname = re.sub("'","''",website['gaTrackerData']['empName'])
    else:
        empname = None
    empid=website['gaTrackerData']['empId']
    result = [[jobid,description,jobtitle,empid, empname]]
    return(result)

#company
def company(website):
    if("empName" in website["gaTrackerData"].keys()):
        empname = re.sub("'","''",website['gaTrackerData']['empName'])
    else:
        empname = None
    if("empSize" in website["gaTrackerData"].keys()):
        empSize = website['gaTrackerData']['empSize']
    else:
        empSize = None
    empId=website['gaTrackerData']['empId']
    if("location" in website["gaTrackerData"].keys()):
        location = re.sub("'","''",website['gaTrackerData']['location'])
    else:
        location = None
    locationId=website['gaTrackerData']['locationId']
    if("description" in website["overview"].keys()):
        company_description=re.sub("'","''",website['overview']['description'])
    else:
        company_description = None
    company_foundedYear=website['overview']['foundedYear']
    if("hq" in website["overview"].keys()):
        company_hq=website['overview']['hq']
    else:
        company_hq = None
    if("industry" in website["overview"].keys()):
        company_industry=website['overview']['industry']
    else:
        company_industry = None
    company_industryId=website['overview']['industryId']
    if("revenue" in website["overview"].keys()):
        company_revenue=website['overview']['revenue']
    else:
        company_revenue = None
    if("sector" in website["overview"].keys()):
        company_sector=website['overview']['sector']
    else:
        company_sector = None
    company_sectorId=website['overview']['sectorId']
    if("website" in website["overview"].keys()):
        company_website=website['overview']['website']
    else:
        company_website = None
    if("type" in website["overview"].keys()):
        company_type=website['overview']['type']
    else:
        company_type = None

    ceo_name = None
    if("rating" in website.keys()):
        if("ceo" in website['rating'].keys()):
            if("name" in website['rating']['ceo'].keys()):
                ceo_name=website['rating']['ceo']['name']
    result = [[empId,empname,empSize,location,locationId,company_description,company_foundedYear,company_hq,company_industry,
               company_industryId,company_revenue,company_sector,company_sectorId,company_website,company_type,ceo_name]]
    return(result)

#rating
def rating(website):
    if("rating" not in website.keys()):
        return("No_rating_at_all")
    else:
        empId=website['gaTrackerData']['empId']
        rating_ceoApproval=website['rating']['ceoApproval']
        rating_recommendToFriend=website['rating']['recommendToFriend']
        rating_starRating=website['rating']['starRating']
        ceo_name = rating_ceoRatingsCount = None
        if("ceo" in website['rating'].keys()):
            if("name" in website['rating']['ceo'].keys()):
                ceo_name=website['rating']['ceo']['name']
            if("ratingsCount" in website['rating']['ceo'].keys()):
                rating_ceoRatingsCount=website['rating']['ceo']['ratingsCount']            
        result = [[empId, ceo_name, rating_ceoRatingsCount, rating_ceoApproval, rating_recommendToFriend, rating_starRating]]
        return(result)

#salary
def salary(website):
    if("salaries" not in website['salary'].keys()):
        return("No_salary_at_all")
    else:
        jobid=website['gaTrackerData']['jobId']
        empId=website['gaTrackerData']['empId']
        salary_number=len(website['salary']['salaries'])
        if(salary_number == 0):
            return("No_salary_at_all")
        else:
            result = []
            for s in range(salary_number):
                salary_basePayCount=website['salary']['salaries'][s]['basePayCount']
                salary_jobtitle=website['salary']['salaries'][s]['jobTitle']
                salary_payPeriod=website['salary']['salaries'][s]['payPeriod']
                if("salaryPercentileMap" in website['salary']['salaries'][s].keys()):
                    salary_payPercentile10=website['salary']['salaries'][s]['salaryPercentileMap']['payPercentile10']
                    salary_payPercentile90=website['salary']['salaries'][s]['salaryPercentileMap']['payPercentile90']
                else:
                    salary_payPercentile10 = salary_payPercentile90 = None
                salary_salaryType=website['salary']['salaries'][s]['salaryType']
                result.append([jobid,empId,salary_basePayCount,salary_jobtitle,salary_payPeriod,salary_payPercentile10,salary_payPercentile90,salary_salaryType])
            return(result)

In [6]:
def get_values_from_website(SQL_TABLE, website):
    if(SQL_TABLE == 'job'):
        result = job(website)
    elif(SQL_TABLE == 'company'):
        result = company(website)
    elif(SQL_TABLE == 'rating'):
        result = rating(website)
    elif(SQL_TABLE == 'salary'):
        result = salary(website)
    return(result)

In [7]:
# Prepare SQL statements
def prepare_insert_stmt(SQL_TABLE, result):
    prepared_stmt = "INSERT INTO " + SQL_TABLE + " values (" + (len(result) * "'{}',").rstrip(",") +");"
    if(SQL_TABLE == 'rating'):
        prepared_stmt = prepared_stmt.replace(" values ("," (companyID,ceo_name,ceo_ratingsCount,ceo_approval,recommend_to_friend,overall_starRating) values (")
    if(SQL_TABLE == 'salary'):
        prepared_stmt = prepared_stmt.replace(" values ("," (jobID,companyID,base_pay_count,job_title,pay_period,pay_q10,pay_q90,salary_type) values (")
    stmt = prepared_stmt.format(*(result))
    return(stmt)

In [8]:
def insert_values_sql(SQL_DB, SQL_TABLE, fileID_list): # insert values for id in id_list into SQL_TABLE
    try:
        conn = pymysql.connect(host='localhost', user = 'root', password = psw, database = 'glassdoor') #connect to server
        cursor = conn.cursor()
        cursor.execute("set sql_mode = ''")
        cursor.execute("USE " + SQL_DB)
        for fileID in fileID_list:
            filename=str("data_analyst/"+fileID+".htm")
            if(fileID in ['3489816886','3497927266','3497328969','3336453336','3475218758','3430002592','3494664274','2776977257',
                          '3501028643','3484776072','3437220141','3480565474','3481916232','3463904299','3465101904','3499621441',
                         '3393100582','3475299206','3016603748','3379092565','3494663555','3437819598','3490863701','3496857990']):
                print("This page "+fileID+".htm is Gateway time-out--------------------------------------")
                continue
            print(filename)

            with open(filename,"rb") as file:
                website=json.load(file)
            result = get_values_from_website(SQL_TABLE, website)

            cursor.execute("SELECT companyID FROM " + SQL_TABLE_company);  
            companyid = cursor.fetchall()
            if((result[0][0] in [id[0] for id in companyid]) and (SQL_TABLE == 'company')):
                print("This companyID already exists in the company table.")
                continue
            if(result == 'No_rating_at_all'):
                print("This file doesn't contain detailed ratings information.")
                continue
            if(result=='No_salary_at_all'):
                print("This file doesn't contain detailed salaries information.")
                continue
            # READY to execute sql insert commands
            for one_result in result:
                cursor.execute( prepare_insert_stmt(SQL_TABLE, one_result) )
                conn.commit()

        time.sleep(0.5)
        cursor.close()
        conn.close()
    except IOError as e:
        pass
        print(e)

In [9]:
with open("jobs_ids_0225.txt","r") as file:
    id_num=file.readlines()
for i in range(len(id_num)):
    id_num[i]=re.sub("\n","",id_num[i])
id_number=pd.DataFrame(id_num)
id_number.columns=['id']
unique_id=id_number["id"].unique()
len(unique_id)

1730

In [11]:
insert_values_sql(SQL_DB, SQL_TABLE_job,unique_id)

data_analyst/3501649697.htm
data_analyst/3456364672.htm
data_analyst/3478565329.htm
data_analyst/3478524160.htm
data_analyst/3464740229.htm
data_analyst/3431946234.htm
data_analyst/3395580482.htm
data_analyst/3496579361.htm
data_analyst/3441680493.htm
data_analyst/3438110795.htm
data_analyst/3467042951.htm
data_analyst/3318697673.htm
data_analyst/3414418309.htm
data_analyst/3474721379.htm
data_analyst/3417817522.htm
data_analyst/3469911803.htm
data_analyst/3042963913.htm
data_analyst/3379431479.htm
data_analyst/3436465921.htm
data_analyst/3473440949.htm
data_analyst/3467596954.htm
data_analyst/3391836921.htm
data_analyst/3475147873.htm
data_analyst/3469858719.htm
data_analyst/3480511216.htm
data_analyst/3481612251.htm
data_analyst/3500586824.htm
data_analyst/3491474507.htm
data_analyst/3497109161.htm
data_analyst/3325221819.htm
data_analyst/3463171767.htm
data_analyst/3425978386.htm
data_analyst/3427465089.htm
data_analyst/3500296601.htm
data_analyst/3460046437.htm
data_analyst/3462822

data_analyst/3098800243.htm
data_analyst/3496913355.htm
data_analyst/3503699010.htm
data_analyst/3476049645.htm
data_analyst/3437736738.htm
data_analyst/3504066852.htm
data_analyst/3458521744.htm
data_analyst/3441689833.htm
data_analyst/3504067143.htm
data_analyst/3466708684.htm
data_analyst/3474690389.htm
data_analyst/3493322258.htm
data_analyst/3490696871.htm
data_analyst/3501195673.htm
This page 3475218758.htm is Gateway time-out--------------------------------------
data_analyst/3361846609.htm
data_analyst/3457195961.htm
This page 3430002592.htm is Gateway time-out--------------------------------------
data_analyst/3474712819.htm
data_analyst/3476213259.htm
data_analyst/3318228759.htm
data_analyst/3487749668.htm
data_analyst/3500460863.htm
data_analyst/3480044930.htm
data_analyst/3429681122.htm
data_analyst/3504058901.htm
data_analyst/3486065645.htm
data_analyst/3414367211.htm
data_analyst/3500393379.htm
data_analyst/3480994312.htm
data_analyst/3472962476.htm
data_analyst/348887994

data_analyst/3348521588.htm
data_analyst/3501367978.htm
data_analyst/3489827034.htm
data_analyst/3017835212.htm
data_analyst/3456042662.htm
data_analyst/3460230006.htm
data_analyst/3442537205.htm
data_analyst/3356467869.htm
data_analyst/3398166546.htm
data_analyst/3495227782.htm
data_analyst/2813338329.htm
data_analyst/3441717974.htm
data_analyst/3415341320.htm
data_analyst/3295380132.htm
data_analyst/3503125096.htm
data_analyst/3466287859.htm
data_analyst/3456218338.htm
data_analyst/3466287857.htm
data_analyst/3437219709.htm
data_analyst/3495798869.htm
data_analyst/3324226077.htm
data_analyst/3472573972.htm
data_analyst/3483021771.htm
data_analyst/3357147803.htm
data_analyst/3477085114.htm
data_analyst/3435025452.htm
This page 3501028643.htm is Gateway time-out--------------------------------------
data_analyst/3407137464.htm
data_analyst/3272656011.htm
data_analyst/3481132919.htm
This page 3484776072.htm is Gateway time-out--------------------------------------
data_analyst/347514893

data_analyst/3450631928.htm
data_analyst/3456609009.htm
data_analyst/3473171384.htm
data_analyst/3501632377.htm
data_analyst/3499078334.htm
data_analyst/3445953303.htm
data_analyst/3360712015.htm
data_analyst/3360710922.htm
data_analyst/3463685792.htm
data_analyst/3476047929.htm
data_analyst/3423427354.htm
data_analyst/3434746688.htm
data_analyst/3474110642.htm
data_analyst/3308422962.htm
data_analyst/3466899829.htm
data_analyst/3493072831.htm
data_analyst/2639482380.htm
data_analyst/3498116394.htm
data_analyst/3476051184.htm
data_analyst/3108196696.htm
data_analyst/3477706760.htm
data_analyst/3243306375.htm
data_analyst/3415269109.htm
data_analyst/3453238006.htm
data_analyst/3497551331.htm
data_analyst/3123346317.htm
data_analyst/3400493155.htm
data_analyst/3469086044.htm
data_analyst/3409644235.htm
data_analyst/3504080293.htm
data_analyst/3420592615.htm
data_analyst/3393262230.htm
data_analyst/3449948668.htm
data_analyst/3316504014.htm
data_analyst/3221238736.htm
data_analyst/3477663

data_analyst/3449230840.htm
data_analyst/3502879168.htm
data_analyst/3501892282.htm
data_analyst/3162425936.htm
data_analyst/3475402359.htm
data_analyst/3500155935.htm
data_analyst/3504079025.htm
data_analyst/3296600293.htm
data_analyst/3501376088.htm
data_analyst/3420685977.htm
data_analyst/2405005569.htm
data_analyst/3480004257.htm
data_analyst/3483547182.htm
data_analyst/3503038857.htm
data_analyst/3503073983.htm
data_analyst/3503887846.htm
data_analyst/3501899692.htm
data_analyst/3498367504.htm
data_analyst/3499652727.htm
data_analyst/3450744529.htm
data_analyst/3475063115.htm
data_analyst/3435511264.htm
data_analyst/3503894025.htm
data_analyst/3147101954.htm
data_analyst/3504063440.htm
data_analyst/3355363684.htm
data_analyst/3416300728.htm
data_analyst/3364217412.htm
data_analyst/3423073306.htm
data_analyst/3437818059.htm
data_analyst/3494408233.htm
data_analyst/3474423306.htm
data_analyst/3468680726.htm
data_analyst/3483239637.htm
data_analyst/3491153675.htm
data_analyst/3492941

data_analyst/3500625756.htm


In [12]:
insert_values_sql(SQL_DB, SQL_TABLE_company,unique_id)

data_analyst/3501649697.htm
data_analyst/3456364672.htm
data_analyst/3478565329.htm
data_analyst/3478524160.htm
data_analyst/3464740229.htm
This companyID already exists in the company table.
data_analyst/3431946234.htm
data_analyst/3395580482.htm
data_analyst/3496579361.htm
data_analyst/3441680493.htm
data_analyst/3438110795.htm
data_analyst/3467042951.htm
data_analyst/3318697673.htm
This companyID already exists in the company table.
data_analyst/3414418309.htm
data_analyst/3474721379.htm
data_analyst/3417817522.htm
This companyID already exists in the company table.
data_analyst/3469911803.htm
data_analyst/3042963913.htm
data_analyst/3379431479.htm
data_analyst/3436465921.htm
data_analyst/3473440949.htm
data_analyst/3467596954.htm
data_analyst/3391836921.htm
This companyID already exists in the company table.
data_analyst/3475147873.htm
data_analyst/3469858719.htm
data_analyst/3480511216.htm
data_analyst/3481612251.htm
data_analyst/3500586824.htm
data_analyst/3491474507.htm
data_ana

data_analyst/3447333594.htm
data_analyst/3501894563.htm
This companyID already exists in the company table.
data_analyst/3393230960.htm
This companyID already exists in the company table.
This page 3497328969.htm is Gateway time-out--------------------------------------
This page 3336453336.htm is Gateway time-out--------------------------------------
data_analyst/3417129371.htm
data_analyst/3493967140.htm
This companyID already exists in the company table.
data_analyst/3431084800.htm
data_analyst/3492157088.htm
data_analyst/3483512312.htm
This companyID already exists in the company table.
data_analyst/3410273595.htm
This companyID already exists in the company table.
data_analyst/3413098694.htm
This companyID already exists in the company table.
data_analyst/3488904459.htm
This companyID already exists in the company table.
data_analyst/3183254078.htm
data_analyst/3492278134.htm
This companyID already exists in the company table.
data_analyst/3492704160.htm
data_analyst/3485706180.ht

data_analyst/3497570332.htm
This companyID already exists in the company table.
data_analyst/3415341319.htm
data_analyst/3437815509.htm
data_analyst/3407137533.htm
data_analyst/2622404288.htm
This companyID already exists in the company table.
data_analyst/3434803029.htm
This companyID already exists in the company table.
data_analyst/3150092313.htm
This companyID already exists in the company table.
data_analyst/3490696436.htm
This companyID already exists in the company table.
data_analyst/3478581888.htm
This companyID already exists in the company table.
data_analyst/3475497501.htm
This companyID already exists in the company table.
data_analyst/3475413054.htm
data_analyst/3455657530.htm
This companyID already exists in the company table.
data_analyst/3322845504.htm
data_analyst/3449601531.htm
data_analyst/3496993960.htm
data_analyst/3454330753.htm
data_analyst/3489751839.htm
data_analyst/3454330759.htm
This companyID already exists in the company table.
data_analyst/3471823575.htm


data_analyst/3424526577.htm
data_analyst/3448497822.htm
data_analyst/3398341453.htm
data_analyst/3394115321.htm
This companyID already exists in the company table.
data_analyst/3470742680.htm
This companyID already exists in the company table.
data_analyst/3437761109.htm
data_analyst/3258689963.htm
This companyID already exists in the company table.
data_analyst/3475272185.htm
This companyID already exists in the company table.
data_analyst/3500196556.htm
This companyID already exists in the company table.
data_analyst/3203961253.htm
data_analyst/3324226073.htm
This companyID already exists in the company table.
data_analyst/3493073049.htm
data_analyst/2809040811.htm
This companyID already exists in the company table.
data_analyst/3475676335.htm
This companyID already exists in the company table.
data_analyst/3268709477.htm
data_analyst/3447521357.htm
data_analyst/3464229194.htm
data_analyst/3458647442.htm
data_analyst/3423074541.htm
data_analyst/3348521588.htm
data_analyst/3501367978.

data_analyst/3483572629.htm
data_analyst/3500833144.htm
This companyID already exists in the company table.
data_analyst/3467175628.htm
data_analyst/3481831645.htm
data_analyst/3475505297.htm
data_analyst/3299852414.htm
data_analyst/3477744605.htm
data_analyst/3361832165.htm
data_analyst/3479661449.htm
This companyID already exists in the company table.
data_analyst/3483303528.htm
This companyID already exists in the company table.
data_analyst/3435504176.htm
This companyID already exists in the company table.
data_analyst/3501486312.htm
data_analyst/3416290388.htm
data_analyst/3492507834.htm
This companyID already exists in the company table.
data_analyst/3490372233.htm
data_analyst/3498436297.htm
data_analyst/3429299428.htm
This companyID already exists in the company table.
data_analyst/3477744628.htm
This companyID already exists in the company table.
data_analyst/3480572073.htm
data_analyst/3377977117.htm
data_analyst/3337832649.htm
data_analyst/3503040114.htm
data_analyst/3445882

...

This companyID already exists in the company table.
data_analyst/3470620728.htm
This companyID already exists in the company table.
data_analyst/3474704752.htm
This companyID already exists in the company table.
data_analyst/3395032251.htm
This companyID already exists in the company table.
data_analyst/3400888259.htm
This companyID already exists in the company table.
data_analyst/3337653943.htm
This companyID already exists in the company table.
data_analyst/3484715439.htm
This companyID already exists in the company table.
data_analyst/3378410910.htm
This companyID already exists in the company table.
data_analyst/3449570448.htm
This companyID already exists in the company table.
data_analyst/3449570491.htm
This companyID already exists in the company table.
data_analyst/3498286594.htm
This companyID already exists in the company table.
data_analyst/3437983513.htm
This companyID already exists in the company table.
data_analyst/3475576328.htm
data_analyst/3502119159.htm
data_analyst

data_analyst/3283112663.htm
This companyID already exists in the company table.
data_analyst/3493135392.htm
This companyID already exists in the company table.
data_analyst/3494408289.htm
This companyID already exists in the company table.
data_analyst/2632276700.htm
This companyID already exists in the company table.
data_analyst/3324229451.htm
data_analyst/3203288516.htm
data_analyst/3478781028.htm
data_analyst/3070674562.htm
data_analyst/3476408122.htm
This companyID already exists in the company table.
data_analyst/3476882736.htm
data_analyst/3467798212.htm
This companyID already exists in the company table.
data_analyst/3440501033.htm
This companyID already exists in the company table.
data_analyst/3466287855.htm
This companyID already exists in the company table.
data_analyst/3466287853.htm
This companyID already exists in the company table.
data_analyst/3475262232.htm
This companyID already exists in the company table.
data_analyst/3435507610.htm
This companyID already exists in

data_analyst/3500155935.htm
This companyID already exists in the company table.
data_analyst/3504079025.htm
data_analyst/3296600293.htm
data_analyst/3501376088.htm
This companyID already exists in the company table.
data_analyst/3420685977.htm
data_analyst/2405005569.htm
data_analyst/3480004257.htm
This companyID already exists in the company table.
data_analyst/3483547182.htm
This companyID already exists in the company table.
data_analyst/3503038857.htm
data_analyst/3503073983.htm
data_analyst/3503887846.htm
data_analyst/3501899692.htm
data_analyst/3498367504.htm
data_analyst/3499652727.htm
This companyID already exists in the company table.
data_analyst/3450744529.htm
data_analyst/3475063115.htm
This companyID already exists in the company table.
data_analyst/3435511264.htm
This companyID already exists in the company table.
data_analyst/3503894025.htm
data_analyst/3147101954.htm
data_analyst/3504063440.htm
data_analyst/3355363684.htm
This companyID already exists in the company tab

This companyID already exists in the company table.
data_analyst/3504028468.htm
This companyID already exists in the company table.
data_analyst/3293973202.htm
This companyID already exists in the company table.
This page 3490863701.htm is Gateway time-out--------------------------------------
data_analyst/2984996389.htm
This companyID already exists in the company table.
data_analyst/2850611021.htm
This companyID already exists in the company table.
data_analyst/3325592173.htm
This companyID already exists in the company table.
data_analyst/3472955071.htm
This companyID already exists in the company table.
data_analyst/2984997059.htm
This companyID already exists in the company table.
data_analyst/3390506873.htm
data_analyst/2850608499.htm
This companyID already exists in the company table.
data_analyst/2984996687.htm
This companyID already exists in the company table.
data_analyst/3433636563.htm
This companyID already exists in the company table.
data_analyst/2984996941.htm
This comp

This companyID already exists in the company table.
data_analyst/3487097036.htm
This companyID already exists in the company table.
data_analyst/3503751611.htm
data_analyst/3438992148.htm
This companyID already exists in the company table.
data_analyst/3498089954.htm
data_analyst/3464768367.htm
This companyID already exists in the company table.
data_analyst/3454004747.htm
data_analyst/3108122589.htm
This companyID already exists in the company table.
data_analyst/3443854213.htm
This companyID already exists in the company table.
data_analyst/3498478428.htm
data_analyst/3483328658.htm
This companyID already exists in the company table.
data_analyst/3501962050.htm
This companyID already exists in the company table.
data_analyst/3500625756.htm
This companyID already exists in the company table.


In [13]:
insert_values_sql(SQL_DB, SQL_TABLE_rating,unique_id)

data_analyst/3501649697.htm
data_analyst/3456364672.htm
data_analyst/3478565329.htm
data_analyst/3478524160.htm
data_analyst/3464740229.htm
data_analyst/3431946234.htm
data_analyst/3395580482.htm
data_analyst/3496579361.htm
data_analyst/3441680493.htm
data_analyst/3438110795.htm
data_analyst/3467042951.htm
data_analyst/3318697673.htm
data_analyst/3414418309.htm
data_analyst/3474721379.htm
data_analyst/3417817522.htm
data_analyst/3469911803.htm
data_analyst/3042963913.htm
This file doesn't contain detailed ratings information.
data_analyst/3379431479.htm
data_analyst/3436465921.htm
data_analyst/3473440949.htm
data_analyst/3467596954.htm
data_analyst/3391836921.htm
data_analyst/3475147873.htm
data_analyst/3469858719.htm
data_analyst/3480511216.htm
data_analyst/3481612251.htm
data_analyst/3500586824.htm
data_analyst/3491474507.htm
data_analyst/3497109161.htm
data_analyst/3325221819.htm
data_analyst/3463171767.htm
data_analyst/3425978386.htm
data_analyst/3427465089.htm
data_analyst/3500296

data_analyst/3427748061.htm
data_analyst/3105306071.htm
data_analyst/3361006543.htm
data_analyst/3496294515.htm
data_analyst/3488459939.htm
data_analyst/3498629162.htm
data_analyst/3483460741.htm
data_analyst/3494381157.htm
data_analyst/3466477327.htm
data_analyst/3420612677.htm
data_analyst/3498664926.htm
data_analyst/3492276406.htm
data_analyst/3460791857.htm
data_analyst/3483521691.htm
data_analyst/3492326562.htm
data_analyst/3492192887.htm
This file doesn't contain detailed ratings information.
data_analyst/3401834696.htm
data_analyst/3474401306.htm
data_analyst/3502555137.htm
data_analyst/3502868072.htm
data_analyst/3485761072.htm
data_analyst/3433426901.htm
data_analyst/3464080257.htm
data_analyst/3499965695.htm
data_analyst/3485761043.htm
data_analyst/2861099087.htm
data_analyst/3498629327.htm
This file doesn't contain detailed ratings information.
data_analyst/3306046696.htm
data_analyst/3503125087.htm
data_analyst/3463922151.htm
data_analyst/3098800243.htm
data_analyst/3496913

data_analyst/3438018316.htm
data_analyst/3324226060.htm
data_analyst/3480234731.htm
This page 3494664274.htm is Gateway time-out--------------------------------------
This page 2776977257.htm is Gateway time-out--------------------------------------
data_analyst/3499435055.htm
data_analyst/3322873730.htm
data_analyst/3078751586.htm
data_analyst/3500461068.htm
data_analyst/3501189850.htm
data_analyst/3487876757.htm
data_analyst/3423073962.htm
data_analyst/3493973487.htm
This file doesn't contain detailed ratings information.
data_analyst/3481811259.htm
This file doesn't contain detailed ratings information.
data_analyst/3442004460.htm
data_analyst/3457280920.htm
data_analyst/3498190102.htm
data_analyst/3439405052.htm
data_analyst/3462630895.htm
data_analyst/3487122378.htm
data_analyst/3430393320.htm
data_analyst/3454962765.htm
data_analyst/3462779843.htm
data_analyst/3475262762.htm
data_analyst/3479330827.htm
data_analyst/3439804089.htm
data_analyst/3425698677.htm
data_analyst/335042171

data_analyst/3386574650.htm
data_analyst/3150008378.htm
data_analyst/3474873898.htm
data_analyst/3052149323.htm
data_analyst/3473510535.htm
data_analyst/3504051946.htm
data_analyst/3499125823.htm
data_analyst/3503037852.htm
This file doesn't contain detailed ratings information.
data_analyst/3450620759.htm
data_analyst/3416303638.htm
This file doesn't contain detailed ratings information.
data_analyst/3422123519.htm
data_analyst/3485600986.htm
data_analyst/3481088594.htm
data_analyst/3430223571.htm
data_analyst/3342281759.htm
data_analyst/3478682482.htm
data_analyst/3496841057.htm
data_analyst/3360748380.htm
data_analyst/3353542783.htm
This file doesn't contain detailed ratings information.
data_analyst/3486090470.htm
data_analyst/3426752912.htm
data_analyst/3498099543.htm
data_analyst/3440929833.htm
data_analyst/3466314462.htm
data_analyst/3450524445.htm
data_analyst/3486615616.htm
This file doesn't contain detailed ratings information.
data_analyst/3405715036.htm
data_analyst/3474420

data_analyst/3497063633.htm
data_analyst/3286424567.htm
data_analyst/2750489641.htm
data_analyst/3486768507.htm
data_analyst/1949248759.htm
data_analyst/3485375157.htm
data_analyst/3356475665.htm
data_analyst/3473768857.htm
data_analyst/3344981970.htm
data_analyst/3485044010.htm
data_analyst/3402839954.htm
data_analyst/3496826286.htm
data_analyst/3496327589.htm
data_analyst/3442839839.htm
data_analyst/3463225560.htm
data_analyst/3480118453.htm
data_analyst/3420541638.htm
data_analyst/3502683506.htm
data_analyst/3122509118.htm
data_analyst/3431001155.htm
data_analyst/3483342681.htm
data_analyst/3398139575.htm
data_analyst/3500217344.htm
data_analyst/3504324938.htm
data_analyst/3331302050.htm
data_analyst/3500469424.htm
data_analyst/3430305049.htm
data_analyst/3498461037.htm
data_analyst/3417714150.htm
data_analyst/3413260189.htm
data_analyst/3411962449.htm
data_analyst/3451418587.htm
data_analyst/3465098460.htm
data_analyst/3144549665.htm
data_analyst/3469787629.htm
data_analyst/3421278

data_analyst/3434787414.htm
data_analyst/3425743972.htm
data_analyst/3480765261.htm
data_analyst/3463185676.htm
data_analyst/3495721529.htm
data_analyst/3373171425.htm
data_analyst/3318677347.htm
data_analyst/3433536021.htm
data_analyst/3440178241.htm
data_analyst/3483313455.htm
data_analyst/3379132491.htm
data_analyst/3501420938.htm
data_analyst/3468305947.htm
data_analyst/3466042343.htm
This file doesn't contain detailed ratings information.
data_analyst/3457678319.htm
data_analyst/3456043190.htm
data_analyst/3454059786.htm
data_analyst/3476321175.htm
data_analyst/3323701333.htm
data_analyst/3477856766.htm
This file doesn't contain detailed ratings information.
data_analyst/3460931642.htm
data_analyst/3472849563.htm
data_analyst/3493115842.htm
data_analyst/3404364323.htm
This page 3475299206.htm is Gateway time-out--------------------------------------
data_analyst/3502715164.htm
data_analyst/3431281455.htm
data_analyst/3485635716.htm
This file doesn't contain detailed ratings inform

data_analyst/3487884809.htm
data_analyst/3158102187.htm
data_analyst/3456245556.htm
data_analyst/3482105143.htm
data_analyst/3488230487.htm
data_analyst/3439432794.htm
data_analyst/3463817520.htm
data_analyst/3145239120.htm
data_analyst/3233618065.htm
data_analyst/3460516953.htm
data_analyst/3290747347.htm
data_analyst/3503547095.htm
data_analyst/3500125462.htm
data_analyst/3497720449.htm
data_analyst/3503089487.htm
data_analyst/3503237606.htm
data_analyst/3475267200.htm
data_analyst/3491285287.htm
data_analyst/3503773087.htm
data_analyst/3484452797.htm
data_analyst/3502960294.htm
data_analyst/3426297636.htm
data_analyst/3502294807.htm
data_analyst/3465738063.htm
data_analyst/3492286444.htm
data_analyst/3040375399.htm
data_analyst/3356156874.htm
data_analyst/3503682544.htm
data_analyst/3465561904.htm
data_analyst/3503079080.htm
This file doesn't contain detailed ratings information.
data_analyst/3286424562.htm
data_analyst/3326068223.htm
data_analyst/3498782460.htm
data_analyst/3331301

In [10]:
insert_values_sql(SQL_DB, SQL_TABLE_salary,unique_id)

data_analyst/3501649697.htm
data_analyst/3456364672.htm
data_analyst/3478565329.htm
data_analyst/3478524160.htm
data_analyst/3464740229.htm
data_analyst/3431946234.htm
data_analyst/3395580482.htm
data_analyst/3496579361.htm
data_analyst/3441680493.htm
data_analyst/3438110795.htm
data_analyst/3467042951.htm
data_analyst/3318697673.htm
data_analyst/3414418309.htm
data_analyst/3474721379.htm
data_analyst/3417817522.htm
data_analyst/3469911803.htm
data_analyst/3042963913.htm
This file doesn't contain detailed salaries information.
data_analyst/3379431479.htm
data_analyst/3436465921.htm
data_analyst/3473440949.htm
data_analyst/3467596954.htm
data_analyst/3391836921.htm
data_analyst/3475147873.htm
data_analyst/3469858719.htm
data_analyst/3480511216.htm
data_analyst/3481612251.htm
data_analyst/3500586824.htm
data_analyst/3491474507.htm
data_analyst/3497109161.htm
data_analyst/3325221819.htm
data_analyst/3463171767.htm
data_analyst/3425978386.htm
data_analyst/3427465089.htm
data_analyst/350029

data_analyst/3463169822.htm
This file doesn't contain detailed salaries information.
data_analyst/3379136123.htm
data_analyst/3027339441.htm
data_analyst/3489754777.htm
data_analyst/3491142240.htm
This file doesn't contain detailed salaries information.
data_analyst/3498493607.htm
data_analyst/3265448573.htm
data_analyst/3495953895.htm
data_analyst/3460838524.htm
This file doesn't contain detailed salaries information.
data_analyst/3492503105.htm
This file doesn't contain detailed salaries information.
data_analyst/3415387122.htm
data_analyst/3498782489.htm
data_analyst/3503870628.htm
data_analyst/3485845678.htm
data_analyst/3496257306.htm
data_analyst/3390967096.htm
data_analyst/3498229100.htm
data_analyst/3479156535.htm
data_analyst/3483088153.htm
data_analyst/3439620471.htm
data_analyst/3489121138.htm
data_analyst/3486976030.htm
data_analyst/3427748061.htm
data_analyst/3105306071.htm
data_analyst/3361006543.htm
data_analyst/3496294515.htm
data_analyst/3488459939.htm
data_analyst/349

data_analyst/2437088928.htm
data_analyst/3462164791.htm
data_analyst/3002541776.htm
data_analyst/3456279628.htm
data_analyst/3441119098.htm
data_analyst/3324226070.htm
data_analyst/3467764871.htm
data_analyst/3480235275.htm
data_analyst/2850610953.htm
data_analyst/3498382578.htm
data_analyst/3483590454.htm
data_analyst/3477770104.htm
data_analyst/3454330760.htm
data_analyst/3490339619.htm
This file doesn't contain detailed salaries information.
data_analyst/3303483788.htm
data_analyst/3450810389.htm
data_analyst/3150098493.htm
data_analyst/3304870896.htm
This file doesn't contain detailed salaries information.
data_analyst/3478601293.htm
This file doesn't contain detailed salaries information.
data_analyst/3501345635.htm
data_analyst/3500196549.htm
data_analyst/3430769261.htm
This file doesn't contain detailed salaries information.
data_analyst/3351987922.htm
data_analyst/3501189881.htm
data_analyst/3471876154.htm
data_analyst/3500431175.htm
This file doesn't contain detailed salaries 

data_analyst/3499564357.htm
data_analyst/3504053415.htm
data_analyst/3353513568.htm
data_analyst/3498949438.htm
data_analyst/3500767495.htm
data_analyst/3497966814.htm
data_analyst/3475068980.htm
data_analyst/3474206941.htm
data_analyst/3362137517.htm
data_analyst/3430551868.htm
data_analyst/3482109463.htm
This file doesn't contain detailed salaries information.
data_analyst/3503675038.htm
data_analyst/3495345722.htm
data_analyst/3499125822.htm
data_analyst/3479657031.htm
data_analyst/3435523314.htm
data_analyst/3449254626.htm
data_analyst/3122917089.htm
data_analyst/3485892015.htm
This file doesn't contain detailed salaries information.
data_analyst/3465764941.htm
data_analyst/3475092775.htm
data_analyst/3463695149.htm
data_analyst/3498072605.htm
data_analyst/3500833064.htm
This file doesn't contain detailed salaries information.
data_analyst/3396497407.htm
data_analyst/3465915749.htm
data_analyst/3499471800.htm
data_analyst/3496150138.htm
data_analyst/3490572838.htm
data_analyst/3498

E:\Anaconda3\lib\site-packages\pymysql\cursors.py:170: Warning: (1366, "Incorrect decimal value: 'None' for column 'pay_q10' at row 1")
  result = self._query(query)
E:\Anaconda3\lib\site-packages\pymysql\cursors.py:170: Warning: (1366, "Incorrect decimal value: 'None' for column 'pay_q90' at row 1")
  result = self._query(query)


data_analyst/3402102431.htm
This file doesn't contain detailed salaries information.
data_analyst/3477852663.htm
This file doesn't contain detailed salaries information.
data_analyst/3178321535.htm
This file doesn't contain detailed salaries information.
data_analyst/3493074775.htm
data_analyst/3498289285.htm
data_analyst/3425995628.htm
This file doesn't contain detailed salaries information.
data_analyst/3494134437.htm
data_analyst/3500565992.htm
data_analyst/3370594677.htm
This file doesn't contain detailed salaries information.
data_analyst/3255081604.htm
data_analyst/3501486310.htm
data_analyst/3494947163.htm
This file doesn't contain detailed salaries information.
data_analyst/3323696652.htm
data_analyst/3001281963.htm
This file doesn't contain detailed salaries information.
data_analyst/3360737514.htm
data_analyst/3267314720.htm
data_analyst/3424077641.htm
This file doesn't contain detailed salaries information.
data_analyst/3423076309.htm
This file doesn't contain detailed salar

data_analyst/3480118453.htm
data_analyst/3420541638.htm
data_analyst/3502683506.htm
data_analyst/3122509118.htm
data_analyst/3431001155.htm
data_analyst/3483342681.htm
data_analyst/3398139575.htm
data_analyst/3500217344.htm
data_analyst/3504324938.htm
data_analyst/3331302050.htm
data_analyst/3500469424.htm
data_analyst/3430305049.htm
data_analyst/3498461037.htm
data_analyst/3417714150.htm
data_analyst/3413260189.htm
data_analyst/3411962449.htm
data_analyst/3451418587.htm
data_analyst/3465098460.htm
data_analyst/3144549665.htm
data_analyst/3469787629.htm
data_analyst/3421278758.htm
data_analyst/3360742530.htm
data_analyst/3436680921.htm
data_analyst/3480272382.htm
data_analyst/3442786135.htm
data_analyst/3472855962.htm
data_analyst/3432021388.htm
data_analyst/3477875310.htm
data_analyst/3464920652.htm
data_analyst/3478152696.htm
data_analyst/3293333349.htm
data_analyst/3498273646.htm
data_analyst/3429659641.htm
data_analyst/3442828630.htm
data_analyst/3438044213.htm
data_analyst/3503034

data_analyst/3431080079.htm
data_analyst/3492309700.htm
data_analyst/3464721054.htm
data_analyst/3489884881.htm
data_analyst/3214771972.htm
data_analyst/3455264775.htm
data_analyst/3477796619.htm
data_analyst/3336480386.htm
data_analyst/3474876179.htm
data_analyst/3415859775.htm
data_analyst/3437311518.htm
data_analyst/3503795537.htm
data_analyst/3395335904.htm
data_analyst/3492298127.htm
data_analyst/3434787414.htm
data_analyst/3425743972.htm
data_analyst/3480765261.htm
data_analyst/3463185676.htm
data_analyst/3495721529.htm
data_analyst/3373171425.htm
data_analyst/3318677347.htm
data_analyst/3433536021.htm
data_analyst/3440178241.htm
data_analyst/3483313455.htm
data_analyst/3379132491.htm
data_analyst/3501420938.htm
data_analyst/3468305947.htm
data_analyst/3466042343.htm
This file doesn't contain detailed salaries information.
data_analyst/3457678319.htm
data_analyst/3456043190.htm
data_analyst/3454059786.htm
data_analyst/3476321175.htm
data_analyst/3323701333.htm
data_analyst/347785

data_analyst/2984996475.htm
data_analyst/3431929235.htm
data_analyst/3459616313.htm
data_analyst/3458321152.htm
data_analyst/3490385215.htm
data_analyst/3463697574.htm
data_analyst/3397979835.htm
data_analyst/3493135051.htm
This file doesn't contain detailed salaries information.
data_analyst/3374247363.htm
data_analyst/3258340305.htm
data_analyst/3260944578.htm
data_analyst/3494408396.htm
data_analyst/3482493532.htm
data_analyst/3495589588.htm
data_analyst/3408534973.htm
data_analyst/3453516014.htm
data_analyst/3483802103.htm
data_analyst/3489630965.htm
data_analyst/3498621542.htm
data_analyst/3404711530.htm
data_analyst/3489831386.htm
data_analyst/3493384103.htm
This file doesn't contain detailed salaries information.
data_analyst/3503339947.htm
data_analyst/3466811543.htm
data_analyst/3495300813.htm
data_analyst/3436087136.htm
data_analyst/3484827227.htm
data_analyst/3482071711.htm
data_analyst/3484653540.htm
data_analyst/3374276963.htm
data_analyst/3400531142.htm
data_analyst/34755

# SELECT values in 4 sql tables

## some info about the number of records
1730 files in total, 24 of them shows "Gateway time-out", 1706 files contain useful information

1. job[1706 rows]: all 1706 files has a unique jobID
2. company[889 rows]: in the 1706 files, only 889 unique companyID
3. salary[6693 rows]: in the 1706 files, only 1458 jobIDs have corresponding salary information, so only 1458 unique jobID in this table; And one jobID can have many salaries for different jobTitle, payPeriod, salaryType
4. rating[1589 rows]: ratings are given for company, not job; in the 889 unique companys, only 885 has ratings information; one company can have more than one rating.     e.g. SELECT * FROM rating WHERE companyID = 326527[this id has 21 ratings, and there are 2 different ceo_approval scores, 3 different recommend_to_friend scores, 2 different overall_starRating scores];


In [15]:
conn = pymysql.connect(host='localhost', user = 'root', password = psw, database = 'glassdoor')
cursor = conn.cursor()

In [16]:
# FOR JOB
query = "USE " + SQL_DB
print(query)
cursor.execute(query);

query = "SELECT * FROM " + SQL_TABLE_job
print(query)
cursor.execute(query);  
job = cursor.fetchall()
job

USE glassdoor
SELECT * FROM job


((1214279060,
  "<strong>SUMMARY</strong>\n<br/><br/>\nProduce and service a book of Employee Benefits business. Represent Bolton &amp; Company at various industry functions.\n<br/><br/>\n<strong>ESSENTIAL DUTIES AND RESPONSIBILITIES</strong>\n<br/><br/>\nOther duties may be assigned.\n<ul>\n\t<li>Attend Assurex meetings, CAIB meetings and selected meetings representing Bolton &amp; Company.</li>\t<li>Support relationship with Employers Group.</li>\t<li>Additional work functions that may be requested by management.</li>\t<li>Coordinate service delivery and retention of produced accounts.</li>\t<li>Actively solicit and consistently present new business opportunities to the Company and meet/exceed new business goals as set from time to time.</li>\t<li>Maintain and grow knowledge base in the areas of insurance and non-insurance products, and individual sales abilities/skills.</li>\t<li>Work with existing client and potential clients to become a &quot;trusted advisor&quot; or &quot;consult

In [17]:
# FOR COMPANY
query = "SELECT * FROM " + SQL_TABLE_company
print(query)
cursor.execute(query);  
company = cursor.fetchall()
company

SELECT * FROM company


((0,
  'None',
  'None',
  'San Francisco',
  1147401,
  'None',
  0,
  'None',
  'None',
  0,
  'None',
  'None',
  0,
  'None',
  'None',
  'None'),
 (97,
  'Best Buy',
  '10000--1',
  'San Francisco',
  1147401,
  'Best Buy is a leading provider of technology products, services and solutions. The company offers expert service at an unbeatable price more than 1.5 billion times a year to the consumers, small business owners and educators who visit our stores, engage with Geek Squad agents or use BestBuy.com or the Best Buy app.  As for our workforce, our employees’ knowledge, passion, and commitment are recognized through pay, benefits and other rewards that are among the best in the industry, including an industry-leading employee discount on the latest and greatest products. We at Best Buy work hard every day to enrich the lives of consumers through technology, whether they come to us online, visit our stores or invite us into their homes. We do this by solving technology problems a

In [18]:
# FOR RATING
query = "SELECT * FROM " + SQL_TABLE_rating
print(query)
cursor.execute(query);  
rating = cursor.fetchall()
rating

SELECT * FROM rating


((1,
  2464640,
  'Alison Darcy',
  4,
  Decimal('1.000'),
  Decimal('0.800'),
  Decimal('3.700')),
 (2,
  892967,
  'Rob Rosania',
  51,
  Decimal('0.880'),
  Decimal('0.840'),
  Decimal('4.400')),
 (3,
  639426,
  'Emmett Shear',
  174,
  Decimal('0.610'),
  Decimal('0.590'),
  Decimal('3.400')),
 (4,
  1087348,
  'Tyson Quick',
  30,
  Decimal('0.970'),
  Decimal('0.920'),
  Decimal('4.900')),
 (5,
  639426,
  'Emmett Shear',
  174,
  Decimal('0.610'),
  Decimal('0.590'),
  Decimal('3.400')),
 (6,
  216924,
  'Leslie Moulton-Post',
  4,
  Decimal('1.000'),
  Decimal('0.660'),
  Decimal('3.600')),
 (7,
  784446,
  'Sean George',
  29,
  Decimal('1.000'),
  Decimal('0.820'),
  Decimal('4.200')),
 (8,
  447133,
  'Victor Ho',
  145,
  Decimal('0.920'),
  Decimal('0.760'),
  Decimal('3.900')),
 (9, 716052, '', 2, Decimal('0.000'), Decimal('0.580'), Decimal('3.800')),
 (10,
  791120,
  'Jason Langheier',
  40,
  Decimal('0.650'),
  Decimal('0.680'),
  Decimal('4.000')),
 (11,
  330195,
 

In [19]:
# FOR SALARY
query = "SELECT * FROM " + SQL_TABLE_salary
print(query)
cursor.execute(query);  
salary = cursor.fetchall()
salary

SELECT * FROM salary


((1,
  3501649697,
  2464640,
  1,
  'Intern',
  'HOURLY',
  Decimal('24.030'),
  Decimal('25.930'),
  'employer'),
 (2,
  3501649697,
  2464640,
  1,
  'CFO',
  'ANNUAL',
  Decimal('144330.020'),
  Decimal('155485.190'),
  'employer'),
 (3,
  3501649697,
  2464640,
  1,
  'Investor Relations Manager',
  'ANNUAL',
  Decimal('98461.340'),
  Decimal('105146.560'),
  'employer'),
 (4,
  3456364672,
  892967,
  5,
  'Sales Associate',
  'HOURLY',
  Decimal('20.000'),
  Decimal('29.780'),
  'employer'),
 (5,
  3456364672,
  892967,
  3,
  'Accounting Associate',
  'ANNUAL',
  Decimal('56002.140'),
  Decimal('67655.590'),
  'employer'),
 (6,
  3456364672,
  892967,
  3,
  'Senior Property Manager',
  'ANNUAL',
  Decimal('79509.270'),
  Decimal('170147.920'),
  'employer'),
 (7,
  3456364672,
  892967,
  2,
  'General Manager',
  'ANNUAL',
  Decimal('58893.980'),
  Decimal('132110.150'),
  'employer'),
 (8,
  3456364672,
  892967,
  2,
  'Anonymous',
  'ANNUAL',
  Decimal('111356.340'),
  Dec

In [20]:
# END the cursor and connection
cursor.close()
conn.close()